<a href="https://colab.research.google.com/github/georgeka98/4_in_a_row_AI/blob/master/nb/Llama3.2_(1B_and_3B)-Conversational.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

To run this, press "*Runtime*" and press "*Run all*" on a **free** Tesla T4 Google Colab instance!
<div class="align-center">
<a href="https://unsloth.ai/"><img src="https://github.com/unslothai/unsloth/raw/main/images/unsloth%20new%20logo.png" width="115"></a>
<a href="https://discord.gg/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/Discord button.png" width="145"></a>
<a href="https://docs.unsloth.ai/"><img src="https://github.com/unslothai/unsloth/blob/main/images/documentation%20green%20button.png?raw=true" width="125"></a></a> Join Discord if you need help + ⭐ <i>Star us on <a href="https://github.com/unslothai/unsloth">Github</a> </i> ⭐
</div>

To install Unsloth on your own computer, follow the installation instructions on our Github page [here](https://docs.unsloth.ai/get-started/installing-+-updating).

You will learn how to do [data prep](#Data), how to [train](#Train), how to [run the model](#Inference), & [how to save it](#Save)

Visit our docs for all our [model uploads](https://docs.unsloth.ai/get-started/all-our-models) and [notebooks](https://docs.unsloth.ai/get-started/unsloth-notebooks).


### News

**[NEW] We've fixed many bugs in Phi-4** which greatly increases Phi-4's accuracy. See our [blogpost](https://unsloth.ai/blog/phi4)

[NEW] You can view all Phi-4 model uploads with our bug fixes including [dynamic 4-bit quants](https://unsloth.ai/blog/dynamic-4bit), GGUF & more [here](https://huggingface.co/collections/unsloth/phi-4-all-versions-677eecf93784e61afe762afa)

[NEW] As of Novemeber 2024, Unsloth now supports [vision finetuning](https://unsloth.ai/blog/vision)!


### Installation

In [ ]:
%%capture
!pip install zipfile

In [ ]:
from google.colab import drive
drive.mount("/content/drive")

In [ ]:
!unzip -t outputs.zip

Archive:  outputs.zip
    testing: outputs/                 OK
    testing: outputs/.DS_Store        OK
    testing: __MACOSX/outputs/._.DS_Store   OK
    testing: outputs/checkpoint-5900/   OK
    testing: outputs/checkpoint-5900/adapter_model.safetensors   OK
    testing: __MACOSX/outputs/checkpoint-5900/._adapter_model.safetensors   OK
    testing: outputs/checkpoint-5900/rng_state.pth   OK
    testing: __MACOSX/outputs/checkpoint-5900/._rng_state.pth   OK
    testing: outputs/checkpoint-5900/tokenizer_config.json   OK
    testing: __MACOSX/outputs/checkpoint-5900/._tokenizer_config.json   OK
    testing: outputs/checkpoint-5900/special_tokens_map.json   OK
    testing: __MACOSX/outputs/checkpoint-5900/._special_tokens_map.json   OK
    testing: outputs/checkpoint-5900/optimizer.pt   OK
    testing: __MACOSX/outputs/checkpoint-5900/._optimizer.pt   OK
    testing: outputs/checkpoint-5900/scheduler.pt   OK
    testing: __MACOSX/outputs/checkpoint-5900/._scheduler.pt   OK
    testing:

In [ ]:
import zipfile
import os

# Check if the file exists
print(os.path.exists("outputs.zip"))

# Extract the ZIP file
with zipfile.ZipFile("outputs.zip", 'r') as zip_ref:
    zip_ref.extractall("outputs")  # Specify the output directory


True


In [ ]:
%%capture
# Normally using pip install unsloth is enough

# Temporarily as of Jan 31st 2025, Colab has some issues with Pytorch
# Using pip install unsloth will take 3 minutes, whilst the below takes <1 minute:
!pip install --no-deps bitsandbytes accelerate xformers==0.0.29 peft trl triton
!pip install --no-deps cut_cross_entropy unsloth_zoo
!pip install sentencepiece protobuf datasets huggingface_hub hf_transfer
!pip install --no-deps unsloth
!pip install detoxify

In [ ]:
!mkdir -p ~/.kaggle
!mv kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json

In [ ]:
!kaggle datasets download -d sherinclaudia/sarcastic-comments-on-reddit

In [ ]:
import zipfile

with zipfile.ZipFile("sarcastic-comments-on-reddit.zip", 'r') as zip_ref:
    zip_ref.extractall("data")  # Extract to a folder named "data"


In [ ]:
import os
print(os.listdir("data"))


['train-balanced-sarcasm.csv']


### Unsloth

In [ ]:
from unsloth import FastLanguageModel
import torch
max_seq_length = 2048 # Choose any! We auto support RoPE Scaling internally!
dtype = None # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
load_in_4bit = True # Use 4bit quantization to reduce memory usage. Can be False.

# 4bit pre quantized models we support for 4x faster downloading + no OOMs.
fourbit_models = [
    "unsloth/Meta-Llama-3.1-8B-bnb-4bit",      # Llama-3.1 2x faster
    "unsloth/Meta-Llama-3.1-8B-Instruct-bnb-4bit",
    "unsloth/Meta-Llama-3.1-70B-bnb-4bit",
    "unsloth/Meta-Llama-3.1-405B-bnb-4bit",    # 4bit for 405b!
    "unsloth/Mistral-Small-Instruct-2409",     # Mistral 22b 2x faster!
    "unsloth/mistral-7b-instruct-v0.3-bnb-4bit",
    "unsloth/Phi-3.5-mini-instruct",           # Phi-3.5 2x faster!
    "unsloth/Phi-3-medium-4k-instruct",
    "unsloth/gemma-2-9b-bnb-4bit",
    "unsloth/gemma-2-27b-bnb-4bit",            # Gemma 2x faster!

    "unsloth/Llama-3.2-1B-bnb-4bit",           # NEW! Llama 3.2 models
    "unsloth/Llama-3.2-1B-Instruct-bnb-4bit",
    "unsloth/Llama-3.2-3B-bnb-4bit",
    "unsloth/Llama-3.2-3B-Instruct-bnb-4bit",

    "unsloth/Llama-3.3-70B-Instruct-bnb-4bit" # NEW! Llama 3.3 70B!
] # More models at https://huggingface.co/unsloth

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "unsloth/Meta-Llama-3.1-8B", # or choose "unsloth/Llama-3.2-1B-Instruct"
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
    quantization_config={"bnb_4bit_compute_dtype": torch.float16},  # Add this
    # quantization_config={"load_in_8bit": True},  # 8-bit quantization
    # token = "hf_...", # use one if using gated models like meta-llama/Llama-2-7b-hf
)

We now add LoRA adapters so we only need to update 1 to 10% of all parameters!

In [ ]:
import copy

model = FastLanguageModel.get_peft_model(
    model,
    r = 16, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj",],
    lora_alpha = 16,
    lora_dropout = 0.1, # Supports any, but = 0 is optimized
    bias = "none",    # Supports any, but = "none" is optimized
    # [NEW] "unsloth" uses 30% less VRAM, fits 2x larger batch sizes!
    use_gradient_checkpointing = "unsloth", # True or "unsloth" for very long context
    random_state = 3407,
    use_rslora = False,  # We support rank stabilized LoRA
    loftq_config = None, # And LoftQ
)


# Assuming `model` is your original model
model_before_finetuning = copy.deepcopy(model)

<a name="Data"></a>
### Data Prep
We now use the `Llama-3.1` format for conversation style finetunes. We use [Maxime Labonne's FineTome-100k](https://huggingface.co/datasets/mlabonne/FineTome-100k) dataset in ShareGPT style. But we convert it to HuggingFace's normal multiturn format `("role", "content")` instead of `("from", "value")`/ Llama-3 renders multi turn conversations like below:

```
<|begin_of_text|><|start_header_id|>user<|end_header_id|>

Hello!<|eot_id|><|start_header_id|>assistant<|end_header_id|>

Hey there! How are you?<|eot_id|><|start_header_id|>user<|end_header_id|>

I'm great thanks!<|eot_id|>
```

We use our `get_chat_template` function to get the correct chat template. We support `zephyr, chatml, mistral, llama, alpaca, vicuna, vicuna_old, phi3, llama3` and more.

In [ ]:
from unsloth.chat_templates import get_chat_template

tokenizer = get_chat_template(
    tokenizer,
    chat_template = "llama-3.1",
)

def formatting_prompts_func(examples):
    convos = examples["conversations"]
    texts = [tokenizer.apply_chat_template(convo, tokenize = False, add_generation_prompt = False) for convo in convos]
    return { "text" : texts, }
pass

from datasets import load_dataset
dataset = load_dataset("mlabonne/FineTome-100k", split = "train")

README.md:   0%|          | 0.00/982 [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/117M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/100000 [00:00<?, ? examples/s]

We now use `standardize_sharegpt` to convert ShareGPT style datasets into HuggingFace's generic format. This changes the dataset from looking like:
```
{"from": "system", "value": "You are an assistant"}
{"from": "human", "value": "What is 2+2?"}
{"from": "gpt", "value": "It's 4."}
```
to
```
{"role": "system", "content": "You are an assistant"}
{"role": "user", "content": "What is 2+2?"}
{"role": "assistant", "content": "It's 4."}
```

In [ ]:
from unsloth.chat_templates import standardize_sharegpt
dataset = standardize_sharegpt(dataset)
dataset = dataset.map(formatting_prompts_func, batched = True,)

Standardizing format:   0%|          | 0/100000 [00:00<?, ? examples/s]

Map:   0%|          | 0/100000 [00:00<?, ? examples/s]

We look at how the conversations are structured for item 5:

In [ ]:
dataset[5]["conversations"]

[{'content': 'How do astronomers determine the original wavelength of light emitted by a celestial body at rest, which is necessary for measuring its speed using the Doppler effect?',
  'role': 'user'},
 {'content': 'Astronomers make use of the unique spectral fingerprints of elements found in stars. These elements emit and absorb light at specific, known wavelengths, forming an absorption spectrum. By analyzing the light received from distant stars and comparing it to the laboratory-measured spectra of these elements, astronomers can identify the shifts in these wavelengths due to the Doppler effect. The observed shift tells them the extent to which the light has been redshifted or blueshifted, thereby allowing them to calculate the speed of the star along the line of sight relative to Earth.',
  'role': 'assistant'}]

And we see how the chat template transformed these conversations.

**[Notice]** Llama 3.1 Instruct's default chat template default adds `"Cutting Knowledge Date: December 2023\nToday Date: 26 July 2024"`, so do not be alarmed!

In [ ]:
dataset[5]["text"]

'<|begin_of_text|><|start_header_id|>system<|end_header_id|>\n\nCutting Knowledge Date: December 2023\nToday Date: 26 July 2024\n\n<|eot_id|><|start_header_id|>user<|end_header_id|>\n\nHow do astronomers determine the original wavelength of light emitted by a celestial body at rest, which is necessary for measuring its speed using the Doppler effect?<|eot_id|><|start_header_id|>assistant<|end_header_id|>\n\nAstronomers make use of the unique spectral fingerprints of elements found in stars. These elements emit and absorb light at specific, known wavelengths, forming an absorption spectrum. By analyzing the light received from distant stars and comparing it to the laboratory-measured spectra of these elements, astronomers can identify the shifts in these wavelengths due to the Doppler effect. The observed shift tells them the extent to which the light has been redshifted or blueshifted, thereby allowing them to calculate the speed of the star along the line of sight relative to Earth.<|

<a name="Train"></a>
### Train the model
Now let's use Huggingface TRL's `SFTTrainer`! More docs here: [TRL SFT docs](https://huggingface.co/docs/trl/sft_trainer). We do 60 steps to speed things up, but you can set `num_train_epochs=1` for a full run, and turn off `max_steps=None`. We also support TRL's `DPOTrainer`!

In [ ]:
alpaca_prompt = """Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.

### Instruction:
{}

### Input:
{}

### Response:
{}"""

EOS_TOKEN = tokenizer.eos_token # Must add EOS_TOKEN
def formatting_prompts_func(examples):
    conversations = examples["conversations"]
    texts = []
    for conversation in conversations:
        # Must add EOS_TOKEN, otherwise your generation will go on forever!
        input_text = conversation[0]["value"]
        output_text = conversation[1]["value"]

        text = alpaca_prompt.format("Generate a funny response", input_text, output_text) + EOS_TOKEN
        texts.append(text)
    return { "text" : texts, }
pass

from datasets import load_dataset
dataset = load_dataset("ZSvedic/humor-chains", split = "train")
dataset = dataset.map(formatting_prompts_func, batched = True,)

In [ ]:
from datasets import Dataset
import pandas as pd

# Load the dataset
df = pd.read_csv("data/train-balanced-sarcasm.csv")

# Display first few rows
print(df.head())
print(df.columns)

# Select the relevant text column
df = df.rename(columns={"comment": "text"})  # Ensure the key is "text" for fine-tuning


# Remove any NaN values (if present)
df = df.dropna(subset=["text", "ups", "downs"])  # Ensure "ups" and "downs" are not NaN

# **Filter the dataset based on 'ups' and 'downs' values**
df = df[(df["ups"] > 50) & (df["downs"] > -10)]

# Convert to Hugging Face dataset
dataset = Dataset.from_pandas(df)

# Split dataset (90% train, 10% validation)
dataset = dataset.train_test_split(test_size=0.1)

# Alpaca-style prompt template
alpaca_prompt = """Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.

### Instruction:
{}

### Input:
{}

### Response:
{}"""

EOS_TOKEN = tokenizer.eos_token  # Must add EOS_TOKEN

def formatting_prompts_func(examples):
    texts = []

    # Extract subreddit as input and parent_comment as output
    print(examples)
    for sub, parent in zip(examples["subreddit"], examples["parent_comment"]):
        input_text = sub  # Use the subreddit name as input
        output_text = parent  # Use the parent_comment as output

        # Format using Alpaca-style prompt
        text = alpaca_prompt.format("Generate a funny response", input_text, output_text) + EOS_TOKEN
        texts.append(text)

    return {"text": texts}

# Apply the function to the filtered dataset
dataset = dataset["train"].map(formatting_prompts_func, batched=True)

num_rows = df.shape[0]
print(f"Number of rows in the dataset: {num_rows}")

   label                                            comment     author  \
0      0                                         NC and NH.  Trumpbart   
1      0  You do know west teams play against west teams...  Shbshb906   
2      0  They were underdogs earlier today, but since G...   Creepeth   
3      0  This meme isn't funny none of the "new york ni...  icebrotha   
4      0                    I could use one of those tools.  cush2push   

            subreddit  score  ups  downs     date          created_utc  \
0            politics      2   -1     -1  2016-10  2016-10-16 23:55:23   
1                 nba     -4   -1     -1  2016-11  2016-11-01 00:24:10   
2                 nfl      3    3      0  2016-09  2016-09-22 21:45:37   
3  BlackPeopleTwitter     -8   -1     -1  2016-10  2016-10-18 21:03:47   
4  MaddenUltimateTeam      6   -1     -1  2016-12  2016-12-30 17:00:13   

                                      parent_comment  
0  Yeah, I get that argument. At this point, I'd ...  


Map:   0%|          | 0/14725 [00:00<?, ? examples/s]

{'label': [1, 1, 0, 1, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 1, 1, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 0, 1, 1, 0, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 1, 1, 0, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 0, 0, 1, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 0,

In [ ]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch.nn.functional as F
from detoxify import Detoxify

# Step 1: Manual Keyword-Based Filtering
def filter_offensive_data(df, column="text"):
    """Removes offensive content based on predefined keywords."""
    hate_categories = [
        "nigga", "nigger", "black people", "white people", "fat people", "stupid people",
        "gay people", "racist people", "ignorant people", "rude people", "old people",
        "pregnant people", "cunt", "sexist people", "chinese people", "indian people",
        "retard", "bipolar people", "jewish people", "ghetto people", "rich people"
    ]

    df[column] = df[column].astype(str).str.lower()

    # Keep only rows that do not contain offensive words
    df_filtered = df[~df[column].str.contains('|'.join(hate_categories), regex=True)]

    return df_filtered

# Step 2: Apply Bias Filtering (Method from OSF Paper)
def detect_bias(text):
    """
    Uses rule-based filtering inspired by the OSF paper to remove biased humor.
    Example: Detect implicit racial, gender, or disability bias in humor.
    """
    biased_phrases = [
        "as a woman", "as a black person", "as a gay man", "for a disabled person",
        "surprisingly smart for", "must be on welfare", "can't drive", "don't belong"
    ]

    for phrase in biased_phrases:
        if phrase in text.lower():
            return True  # Mark as biased

    return False  # Text passes the bias check

def classify_offensive_hatexplain(text):


    # Step 3: Offensive Content Detection using HateXplain
    device = "cuda" if torch.cuda.is_available() else "cpu"

    # Load the HateXplain model and tokenizer
    model_name = "Hate-speech-CNERG/bert-base-uncased-hatexplain"
    tokenizer_hatexplain = AutoTokenizer.from_pretrained(model_name)
    model_hatexplain = AutoModelForSequenceClassification.from_pretrained(model_name).to(device)

    inputs = tokenizer_hatexplain(text, return_tensors="pt", truncation=True, padding=True).to(device)

    with torch.no_grad():
        outputs = model_hatexplain(**inputs)
        logits = outputs.logits.cpu()  # Move to CPU
        probs = F.softmax(logits, dim=-1)  # Convert logits to probabilities

    # Extract probabilities for each class
    normal_prob = probs[0][0]
    offensive_prob = probs[0][1]
    hate_prob = probs[0][2]

    # Decision logic
    if normal_prob < 0.02:  # If normal class is almost impossible (<2%), take the most likely class
        predicted_label = torch.argmax(probs, dim=-1).item()
    elif offensive_prob < 0.8 and hate_prob < 0.8:  # If both offensive & hate are weak (<8%), return Normal
        predicted_label = 0
    else:  # Otherwise, pick the strongest class
        predicted_label = torch.argmax(probs, dim=-1).item()

    print(f"Probabilities: {probs} -> Predicted: {predicted_label} | Text: {text}")
    return predicted_label

def classify_offensive(text, threshold=0.5):
    # Get toxicity scores using Detoxify
    results = Detoxify('original').predict(text)

    # Find the highest probability label
    highest_label = max(results, key=results.get)
    highest_prob = results[highest_label]

    # Apply threshold: if no category is strong enough, classify as normal
    if highest_prob < threshold:
        predicted_label = "normal"
    else:
        predicted_label = highest_label

    print(f"Probabilities: {results} -> Predicted: {predicted_label} | Text: {text}")
    return predicted_label


tokenizer_config.json:   0%|          | 0.00/40.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.08k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/438M [00:00<?, ?B/s]

In [ ]:
import pandas as pd
import torch
from datasets import Dataset, load_dataset

# Load the first dataset (Kaggle sarcasm dataset)
df1 = pd.read_csv("data/train-balanced-sarcasm.csv")

df1 = df1.rename(columns={"comment": "text"})
df1 = df1.dropna(subset=["text", "ups", "downs"])
df1 = df1[(df1["ups"] > 50) & (df1["downs"] > -10)]
df1 = filter_offensive_data(df1)  # Apply manual filtering

# Convert to Hugging Face dataset
dataset1 = Dataset.from_pandas(df1)
dataset1 = dataset1.train_test_split(test_size=0.1)  # Split dataset

# Load the second dataset (Humor Chains)
dataset2 = load_dataset("ZSvedic/humor-chains", split="train")

# Convert dataset2 to DataFrame
df2 = pd.DataFrame(dataset2)

# Print column names
print("DF2 Columns:", df2.columns.tolist())

# Extract "text" from conversations
def extract_text(convo):
    """Extracts human input and GPT response."""
    if isinstance(convo, list) and len(convo) > 1:
        return convo[1]["value"]  # Get GPT response
    return ""  # Fallback

df2["text"] = df2["conversations"].apply(extract_text)

# Apply bias detection filtering
df1 = df1[~df1["text"].apply(detect_bias)]
df2 = df2[~df2["text"].apply(detect_bias)]

# Apply HateXplain filtering
# df1.loc[:20, "offense_label"] = df1.loc[:20, "text"].apply(lambda x: print(classify_offensive(x)) or classify_offensive(x))
# df2.loc[:20, "offense_label"] = df2.loc[:20, "text"].apply(lambda x: print(classify_offensive(x)) or classify_offensive(x))

df1.loc[:9, "offense_label"] = df1.loc[:9, "text"].apply(lambda x: print(classify_offensive(x)) or classify_offensive(x))
df2.loc[:9, "offense_label"] = df2.loc[:9, "text"].apply(lambda x: print(classify_offensive(x)) or classify_offensive(x))

# df1["offense_label"] = df1["text"].apply(lambda x: print(classify_offensive(x)) or classify_offensive(x))
# df2["offense_label"] = df2["text"].apply(lambda x: print(classify_offensive(x)) or classify_offensive(x))

# Save datasets as CSV files
df1.to_csv("df1_offense_labeled.csv", index=False)
df2.to_csv("df2_offense_labeled.csv", index=False)

model.safetensors:   0%|          | 0.00/438M [00:00<?, ?B/s]

README.md:   0%|          | 0.00/3.79k [00:00<?, ?B/s]

humor-train.jsonl:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

humor-test.jsonl:   0%|          | 0.00/217k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/5844 [00:00<?, ? examples/s]

...

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

Probabilities: {'toxicity': 0.00064006343, 'severe_toxicity': 0.00011742885, 'obscene': 0.00017709061, 'threat': 0.00012085425, 'insult': 0.00017666645, 'identity_attack': 0.00013866613} -> Predicted: normal | Text: The last time I tried cooking books, the IRS got involved and now I'm in witness protection.
normal
Probabilities: {'toxicity': 0.00064006343, 'severe_toxicity': 0.00011742885, 'obscene': 0.00017709061, 'threat': 0.00012085425, 'insult': 0.00017666645, 'identity_attack': 0.00013866613} -> Predicted: normal | Text: The last time I tried cooking books, the IRS got involved and now I'm in witness protection.
Probabilities: {'toxicity': 0.0021020793, 'severe_toxicity': 9.159919e-05, 'obscene': 0.00022740019, 'threat': 0.000101809856, 'insult': 0.00021166082, 'identity_attack': 0.00014710879} -> Predicted: normal | Text: OH! I know, I know!!! It's WHERE to eat out for dinner, RIGHT? I'm right, I'm right, aren't I? I mean, after 31 years of marriage, what else could it possibly b

In [ ]:

df1 = pd.read_csv("df1_offense_labeled.csv")
df2 = pd.read_csv("df2_offense_labeled.csv")

# Remove offensive (label 1) and hate speech (label 2)
df1 = df1[df1["offense_label"] == 0].drop(columns=["offense_label"])
df2 = df2[df2["offense_label"] == 0].drop(columns=["offense_label"])

# Step 4: Formatting for Fine-Tuning
alpaca_prompt = """Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.

### Instruction:
{}

### Input:
{}

### Response:
{}"""

EOS_TOKEN = "<|endoftext|>"

def formatting_prompts_func1(examples):
    texts = []
    for parent, comment in zip(examples["parent_comment"], examples["text"]):
        input_text = parent
        output_text = comment
        text = alpaca_prompt.format("Generate a funny response", input_text, output_text) + EOS_TOKEN
        texts.append(text)
    return {"text": texts}

def formatting_prompts_func2(examples):
    texts = []
    for conversation in examples["conversations"]:
        if isinstance(conversation, list) and len(conversation) > 1:
            input_text = conversation[0]["value"]
            output_text = conversation[1]["value"]
            text = alpaca_prompt.format("Generate a funny response", input_text, output_text) + EOS_TOKEN
            texts.append(text)
    return {"text": texts}

# Apply formatting
dataset1 = dataset1.map(formatting_prompts_func1, batched=True)
dataset2 = dataset2.map(formatting_prompts_func2, batched=True)

# Convert datasets to Pandas for validation
df1 = pd.DataFrame(dataset1["train"])
df2 = pd.DataFrame(dataset2)

# Apply the final filtering step
df1 = filter_offensive_data(df1)
df2 = filter_offensive_data(df2)

# Ensure consistent structure
df1 = df1[["text"]].head(2500)
df2 = df2[["text"]].head(2500)

# Convert back to Hugging Face datasets
formatted_dataset1 = Dataset.from_pandas(df1)
formatted_dataset2 = Dataset.from_pandas(df2)

# Combine datasets
combined_dataset = Dataset.from_pandas(pd.concat([df1, df2], ignore_index=True))

# Save datasets
df1.to_csv("filtered_sarcasm_dataset.csv", index=False)
df2.to_csv("filtered_humor_chains_dataset.csv", index=False)

# Display structure
print("Dataset 1 (Sarcasm) Structure:", df1.head())
print("Dataset 2 (Humor Chains) Structure:", df2.head())

print(f"Total rows in filtered sarcasm dataset: {len(df1)}")
print(f"Total rows in filtered humor chains dataset: {len(df2)}")

Map:   0%|          | 0/14610 [00:00<?, ? examples/s]

Map:   0%|          | 0/1624 [00:00<?, ? examples/s]

Map:   0%|          | 0/5844 [00:00<?, ? examples/s]

Dataset 1 (Sarcasm) Structure:                                                 text
0  below is an instruction that describes a task,...
1  below is an instruction that describes a task,...
2  below is an instruction that describes a task,...
3  below is an instruction that describes a task,...
4  below is an instruction that describes a task,...
Dataset 2 (Humor Chains) Structure:                                                 text
0  below is an instruction that describes a task,...
1  below is an instruction that describes a task,...
2  below is an instruction that describes a task,...
3  below is an instruction that describes a task,...
4  below is an instruction that describes a task,...
Total rows in filtered sarcasm dataset: 2500
Total rows in filtered humor chains dataset: 2500


In [ ]:
pip install peft

In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer
from peft import LoraConfig, get_peft_model
from trl import SFTTrainer
from transformers import TrainingArguments, DataCollatorForSeq2Seq
from unsloth import is_bfloat16_supported

# Define custom loss function
def compute_loss(model, inputs, return_outputs=False):
    labels = inputs.pop("labels")
    outputs = model(**inputs)
    logits = outputs.logits

    # Shift logits and labels to align them
    shift_logits = logits[..., :-1, :].contiguous()
    shift_labels = labels[..., 1:].contiguous()

    # Compute cross-entropy loss
    loss = F.cross_entropy(shift_logits.view(-1, shift_logits.size(-1)), shift_labels.view(-1), ignore_index=-100)

    return (loss, outputs) if return_outputs else loss

print(combined_dataset, combined_dataset.to_dict()["text"])  # Convert row to dictionary for better readability

# Prepare trainer
trainer = SFTTrainer(
    model=model,
    tokenizer=tokenizer,
    train_dataset=combined_dataset,
    dataset_text_field="text",
    max_seq_length=max_seq_length,
    dataset_num_proc=2,
    packing=False,  # Can make training 5x faster for short sequences.
    # compute_loss=compute_loss,
    args=TrainingArguments(
        per_device_train_batch_size=2,
        gradient_accumulation_steps=4,
        warmup_steps=5,
        save_steps = 100,
        max_steps = 5000,
        learning_rate=2e-4,
        fp16 = True,
        bf16 = False,
        logging_steps=1,
        optim="adamw_8bit",
        weight_decay=0.01,
        lr_scheduler_type="linear",
        seed=3407,
        output_dir="outputs",
        report_to="none",
    ),
)


Dataset({
    features: ['text'],
    num_rows: 5000
}) ["below is an instruction that describes a task, paired with an input that provides further context. write a response that appropriately completes the request.\n\n### instruction:\ngenerate a funny response\n\n### input:\nafter he said it, huni would be such a good minlaner. he has amazing mechanics on carry champions but can't play tanks thats like perfect description of midlane xd\n\n### response:\nthey should just put pobelter top, since he gets top 50% of the time in dynamic q anyway.<|endoftext|>", 'below is an instruction that describes a task, paired with an input that provides further context. write a response that appropriately completes the request.\n\n### instruction:\ngenerate a funny response\n\n### input:\nbut to have infinite memory, you will need ram manufactured from unobtainium.\n\n### response:\ntime to kill some blue people.<|endoftext|>', "below is an instruction that describes a task, paired with an input tha

AttributeError: 'Embedding' object has no attribute 'dtype'

In [ ]:
trainer_stats = trainer.train(resume_from_checkpoint = True)

/usr/local/lib/python3.11/dist-packages/transformers/trainer.py:3441: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  torch.load(os.path.join(checkpoint, OPTIMIZER_NAME), map_

We also use Unsloth's `train_on_completions` method to only train on the assistant outputs and ignore the loss on the user's inputs.

In [ ]:
from unsloth.chat_templates import train_on_responses_only
trainer = train_on_responses_only(
    trainer,
    instruction_part = "<|start_header_id|>user<|end_header_id|>\n\n",
    response_part = "<|start_header_id|>assistant<|end_header_id|>\n\n",
)

Map:   0%|          | 0/100000 [00:00<?, ? examples/s]

We verify masking is actually done:

In [ ]:
tokenizer.decode(trainer.train_dataset[5]["input_ids"])

'<|begin_of_text|><|start_header_id|>system<|end_header_id|>\n\nCutting Knowledge Date: December 2023\nToday Date: 26 July 2024\n\n<|eot_id|><|start_header_id|>user<|end_header_id|>\n\nHow do astronomers determine the original wavelength of light emitted by a celestial body at rest, which is necessary for measuring its speed using the Doppler effect?<|eot_id|><|start_header_id|>assistant<|end_header_id|>\n\nAstronomers make use of the unique spectral fingerprints of elements found in stars. These elements emit and absorb light at specific, known wavelengths, forming an absorption spectrum. By analyzing the light received from distant stars and comparing it to the laboratory-measured spectra of these elements, astronomers can identify the shifts in these wavelengths due to the Doppler effect. The observed shift tells them the extent to which the light has been redshifted or blueshifted, thereby allowing them to calculate the speed of the star along the line of sight relative to Earth.<|

In [ ]:
space = tokenizer(" ", add_special_tokens = False).input_ids[0]
tokenizer.decode([space if x == -100 else x for x in trainer.train_dataset[5]["labels"]])

'                                                                \n\nAstronomers make use of the unique spectral fingerprints of elements found in stars. These elements emit and absorb light at specific, known wavelengths, forming an absorption spectrum. By analyzing the light received from distant stars and comparing it to the laboratory-measured spectra of these elements, astronomers can identify the shifts in these wavelengths due to the Doppler effect. The observed shift tells them the extent to which the light has been redshifted or blueshifted, thereby allowing them to calculate the speed of the star along the line of sight relative to Earth.<|eot_id|>'

We can see the System and Instruction prompts are successfully masked!

In [ ]:
# @title Show current memory stats
gpu_stats = torch.cuda.get_device_properties(0)
start_gpu_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
max_memory = round(gpu_stats.total_memory / 1024 / 1024 / 1024, 3)
print(f"GPU = {gpu_stats.name}. Max memory = {max_memory} GB.")
print(f"{start_gpu_memory} GB of memory reserved.")

GPU = Tesla T4. Max memory = 14.748 GB.
2.635 GB of memory reserved.


In [ ]:
trainer_stats = trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs = 1
   \\   /|    Num examples = 100,000 | Num Epochs = 1
O^O/ \_/ \    Batch size per device = 2 | Gradient Accumulation steps = 4
\        /    Total batch size = 8 | Total steps = 60
 "-____-"     Number of trainable parameters = 24,313,856


In [ ]:
# @title Show final memory and time stats
used_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
used_memory_for_lora = round(used_memory - start_gpu_memory, 3)
used_percentage = round(used_memory / max_memory * 100, 3)
lora_percentage = round(used_memory_for_lora / max_memory * 100, 3)
print(f"{trainer_stats.metrics['train_runtime']} seconds used for training.")
print(
    f"{round(trainer_stats.metrics['train_runtime']/60, 2)} minutes used for training."
)
print(f"Peak reserved memory = {used_memory} GB.")
print(f"Peak reserved memory for training = {used_memory_for_lora} GB.")
print(f"Peak reserved memory % of max memory = {used_percentage} %.")
print(f"Peak reserved memory for training % of max memory = {lora_percentage} %.")

446.5262 seconds used for training.
7.44 minutes used for training.
Peak reserved memory = 6.531 GB.
Peak reserved memory for training = 3.896 GB.
Peak reserved memory % of max memory = 44.284 %.
Peak reserved memory for training % of max memory = 26.417 %.


<a name="Inference"></a>
### Inference
Let's run the model! You can change the instruction and input - leave the output blank!

**[NEW] Try 2x faster inference in a free Colab for Llama-3.1 8b Instruct [here](https://colab.research.google.com/drive/1T-YBVfnphoVc8E2E854qF3jdia2Ll2W2?usp=sharing)**

We use `min_p = 0.1` and `temperature = 1.5`. Read this [Tweet](https://x.com/menhguin/status/1826132708508213629) for more information on why.

In [ ]:
FastLanguageModel.for_inference(model)
inputs = tokenizer(
    [
        alpaca_prompt.format(
            "Generate a funny response",
            "Why is eiffel tower so tall",
            ""
        )
    ], return_tensors="pt").to("cuda")

outputs = model.generate(**inputs, max_new_tokens=64, use_cache=True)
tokenizer.batch_decode(outputs)

['<|begin_of_text|>Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.\n\n### Instruction:\nGenerate a funny response\n\n### Input:\nWhy is eiffel tower so tall\n\n### Response:\nBecause Parisians like to have a little extra... **panache**.<|end_of_text|>']

 You can also use a `TextStreamer` for continuous inference - so you can see the generation token by token, instead of waiting the whole time!

In [ ]:
FastLanguageModel.for_inference(model_before_finetuning)
inputs = tokenizer(
    [
        alpaca_prompt.format(
            "Generate a funny response",
            "Why is eiffel tower so tall",
            ""
        )
    ], return_tensors="pt").to("cuda")

outputs = model.generate(**inputs, max_new_tokens=64, use_cache=True)
tokenizer.batch_decode(outputs)

['<|begin_of_text|>Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.\n\n### Instruction:\nGenerate a funny response\n\n### Input:\nWhy is eiffel tower so tall\n\n### Response:\nThe Eiffel Tower is so tall because it was built as a lighthouse. The top of the tower has a lightbulb in it to shine out a beam of light which can be seen for miles. This was to guide boats on the river Seine and other waterways into Paris.<|end_of_text|>']

<a name="Save"></a>
### Saving, loading finetuned models
To save the final model as LoRA adapters, either use Huggingface's `push_to_hub` for an online save or `save_pretrained` for a local save.

**[NOTE]** This ONLY saves the LoRA adapters, and not the full model. To save to 16bit or GGUF, scroll down!

In [ ]:
model.save_pretrained("lora_model")  # Local saving
tokenizer.save_pretrained("lora_model")
# model.push_to_hub("your_name/lora_model", token = "...") # Online saving
# tokenizer.push_to_hub("your_name/lora_model", token = "...") # Online saving

('lora_model/tokenizer_config.json',
 'lora_model/special_tokens_map.json',
 'lora_model/tokenizer.json')

Now if you want to load the LoRA adapters we just saved for inference, set `False` to `True`:

In [ ]:
if False:
    from unsloth import FastLanguageModel
    model, tokenizer = FastLanguageModel.from_pretrained(
        model_name = "lora_model", # YOUR MODEL YOU USED FOR TRAINING
        max_seq_length = max_seq_length,
        dtype = dtype,
        load_in_4bit = load_in_4bit,
    )
    FastLanguageModel.for_inference(model) # Enable native 2x faster inference

messages = [
    {"role": "user", "content": "Describe a tall tower in the capital of France."},
]
inputs = tokenizer.apply_chat_template(
    messages,
    tokenize = True,
    add_generation_prompt = True, # Must add for generation
    return_tensors = "pt",
).to("cuda")

from transformers import TextStreamer
text_streamer = TextStreamer(tokenizer, skip_prompt = True)
_ = model.generate(input_ids = inputs, streamer = text_streamer, max_new_tokens = 128,
                   use_cache = True, temperature = 1.5, min_p = 0.1)

The Eiffel Tower, located in the heart of Paris, stands tall among the city's historic and cultural landmarks. This iron structure, standing at an impressive 324 meters high, offers breathtaking views of the City of Light's iconic landscape. The Eiffel Tower was built for the 1889 World's Fair and has since become a symbol of French engineering and culture.<|eot_id|>


You can also use Hugging Face's `AutoModelForPeftCausalLM`. Only use this if you do not have `unsloth` installed. It can be hopelessly slow, since `4bit` model downloading is not supported, and Unsloth's **inference is 2x faster**.

In [ ]:
if False:
    # I highly do NOT suggest - use Unsloth if possible
    from peft import AutoPeftModelForCausalLM
    from transformers import AutoTokenizer
    model = AutoPeftModelForCausalLM.from_pretrained(
        "lora_model", # YOUR MODEL YOU USED FOR TRAINING
        load_in_4bit = load_in_4bit,
    )
    tokenizer = AutoTokenizer.from_pretrained("lora_model")

### Saving to float16 for VLLM

We also support saving to `float16` directly. Select `merged_16bit` for float16 or `merged_4bit` for int4. We also allow `lora` adapters as a fallback. Use `push_to_hub_merged` to upload to your Hugging Face account! You can go to https://huggingface.co/settings/tokens for your personal tokens.

In [ ]:
# Merge to 16bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_16bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_16bit", token = "")

# Merge to 4bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_4bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_4bit", token = "")

# Just LoRA adapters
if False: model.save_pretrained_merged("model", tokenizer, save_method = "lora",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "lora", token = "")

### GGUF / llama.cpp Conversion
To save to `GGUF` / `llama.cpp`, we support it natively now! We clone `llama.cpp` and we default save it to `q8_0`. We allow all methods like `q4_k_m`. Use `save_pretrained_gguf` for local saving and `push_to_hub_gguf` for uploading to HF.

Some supported quant methods (full list on our [Wiki page](https://github.com/unslothai/unsloth/wiki#gguf-quantization-options)):
* `q8_0` - Fast conversion. High resource use, but generally acceptable.
* `q4_k_m` - Recommended. Uses Q6_K for half of the attention.wv and feed_forward.w2 tensors, else Q4_K.
* `q5_k_m` - Recommended. Uses Q6_K for half of the attention.wv and feed_forward.w2 tensors, else Q5_K.

[**NEW**] To finetune and auto export to Ollama, try our [Ollama notebook](https://colab.research.google.com/drive/1WZDi7APtQ9VsvOrQSSC5DDtxq159j8iZ?usp=sharing)

In [ ]:
# Save to 8bit Q8_0
if False: model.save_pretrained_gguf("model", tokenizer,)
# Remember to go to https://huggingface.co/settings/tokens for a token!
# And change hf to your username!
if False: model.push_to_hub_gguf("hf/model", tokenizer, token = "")

# Save to 16bit GGUF
if False: model.save_pretrained_gguf("model", tokenizer, quantization_method = "f16")
if False: model.push_to_hub_gguf("hf/model", tokenizer, quantization_method = "f16", token = "")

# Save to q4_k_m GGUF
if False: model.save_pretrained_gguf("model", tokenizer, quantization_method = "q4_k_m")
if False: model.push_to_hub_gguf("hf/model", tokenizer, quantization_method = "q4_k_m", token = "")

# Save to multiple GGUF options - much faster if you want multiple!
if False:
    model.push_to_hub_gguf(
        "hf/model", # Change hf to your username!
        tokenizer,
        quantization_method = ["q4_k_m", "q8_0", "q5_k_m",],
        token = "", # Get a token at https://huggingface.co/settings/tokens
    )

Now, use the `model-unsloth.gguf` file or `model-unsloth-Q4_K_M.gguf` file in llama.cpp or a UI based system like Jan or Open WebUI. You can install Jan [here](https://github.com/janhq/jan) and Open WebUI [here](https://github.com/open-webui/open-webui)

And we're done! If you have any questions on Unsloth, we have a [Discord](https://discord.gg/unsloth) channel! If you find any bugs or want to keep updated with the latest LLM stuff, or need help, join projects etc, feel free to join our Discord!

Some other links:
1. Llama 3.2 Conversational notebook. [Free Colab](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3.2_(1B_and_3B)-Conversational.ipynb)
2. Saving finetunes to Ollama. [Free notebook](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3_(8B)-Ollama.ipynb)
3. Llama 3.2 Vision finetuning - Radiography use case. [Free Colab](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3.2_(11B)-Vision.ipynb)
6. See notebooks for DPO, ORPO, Continued pretraining, conversational finetuning and more on our [documentation](https://docs.unsloth.ai/get-started/unsloth-notebooks)!

<div class="align-center">
  <a href="https://unsloth.ai"><img src="https://github.com/unslothai/unsloth/raw/main/images/unsloth%20new%20logo.png" width="115"></a>
  <a href="https://discord.gg/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/Discord.png" width="145"></a>
  <a href="https://docs.unsloth.ai/"><img src="https://github.com/unslothai/unsloth/blob/main/images/documentation%20green%20button.png?raw=true" width="125"></a>

  Join Discord if you need help + ⭐️ <i>Star us on <a href="https://github.com/unslothai/unsloth">Github</a> </i> ⭐️
</div>
